In [1]:
import pandas as pd
from os import path
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.linear_model import LogisticRegression
from sklearn.utils.fixes import loguniform    
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.preprocessing import StandardScaler
from sklearn.neighbors import NearestNeighbors
import pickle
import numpy as np
import os
import json
import csv

In [2]:
DATA_DIR = "../../data"

In [3]:
chen_train = pd.read_csv(path.join(DATA_DIR, "chen/deduplicated/chen_train_data.csv"), index_col=0)
chen_train.head()

Antibody_ID                                              heavy  \
2073        6aod  EVQLVQSGAEVKKPGASVKVSCKASGYTFTGYYMHWVRQAPGQGLE...   
1517        4yny  EVQLVESGGGLVQPGRSLKLSCAASGFTFSNYGMAWVRQTPTKGLE...   
2025        5xcv  EVQLVESGGGLVQPGRSLKLSCAASGFTFSNYGMAWVRQTPTKGLE...   
2070        6and  EVQLVESGGGLVQPGGSLRLSCAASGYEFSRSWMNWVRQAPGKGLE...   
666         2xqy  QVQLQQPGAELVKPGASVKMSCKASGYSFTSYWMNWVKQRPGRGLE...   

                                                  light  Y  
2073  DIVMTKSPSSLSASVGDRVTITCRASQGIRNDLGWYQQKPGKAPKR...  0  
1517  EFVLTQPNSVSTNLGSTVKLSCKRSTGNIGSNYVNWYQQHEGRSPT...  1  
2025  QFVLTQPNSVSTNLGSTVKLSCKRSTGNIGSNYVNWYQQHEGRSPT...  1  
2070  DIQMTQSPSSLSASVGDRVTITCRSSQSIVHSVGNTFLEWYQQKPG...  1  
666   DIVLTQSPASLALSLGQRATISCRASKSVSTSGYSYMYWYQQKPGQ...  0

In [4]:
chen_valid = pd.read_csv(path.join(DATA_DIR, "chen/deduplicated/chen_valid_data.csv"), index_col=0)
chen_test = pd.read_csv(path.join(DATA_DIR, "chen/deduplicated/chen_test_data.csv"))
chen_valid = pd.concat([chen_valid, chen_test])
chen_valid.head()

Antibody_ID                                              heavy  \
2169        6ct7  EVQLVESGGGLVEPGGSLRLSCAVSGFDFEKAWMSWVRQAPGQGLQ...   
1342        4nzu  AVSLVESGGGTVEPGSTLRLSCAASGFTFGSYAFHWVRQAPGDGLE...   
1728        5i8c  QEVLVQSGAEVKKPGASVKVSCRAFGYTFTGNALHWVRQAPGQGLE...   
1729        5i8e  QEVLVQSGAEVKKPGASVKVSCRAFGYTFTGNALHWVRQAPGQGLE...   
2114        6bb4  QVQLQQSDAELVKPGASVKISCKASGYTFTDRTIHWVKQRPEQGLE...   

                                                  light  Y  Unnamed: 0  
2169  SYELTQPPSVSVSPGQTARITCSGEALPMQFAHWYQQRPGKAPVIV...  0         NaN  
1342  DIEMTQSPSSLSASTGDKVTITCQASQDIAKFLDWYQQRPGKTPKL...  0         NaN  
1728  DIQLTQSPSFLSASVGDKVTITCRASQGVRNELAWYQQKPGKAPNL...  1         NaN  
1729  IQLTQSPSFLSASVGDKVTITCRASQGVRNELAWYQQKPGKAPNLL...  0         NaN  
2114  DVQMIQSPSSLSASLGDIVTMTCQASQDTSINLNWFQQKPGKAPKL...  0         NaN

In [5]:
tap_data = pd.read_csv(path.join(DATA_DIR, "tap/TAP_data.csv"))
tap_data.head()

Antibody_ID                                              heavy  \
0  Abagovomab  QVKLQESGAELARPGASVKLSCKASGYTFTNYWMQWVKQRPGQGLD...   
1  Abituzumab  QVQLQQSGGELAKPGASVKVSCKASGYTFSSFWMHWVRQAPGQGLE...   
2   Abrilumab  QVQLVQSGAEVKKPGASVKVSCKVSGYTLSDLSIHWVRQAPGKGLE...   
3   Actoxumab  QVQLVESGGGVVQPGRSLRLSCAASGFSFSNYGMHWVRQAPGKGLE...   
4  Adalimumab  EVQLVESGGGLVQPGRSLRLSCAASGFTFDDYAMHWVRQAPGKGLE...   

                                               light  CDR_length       PSH  \
0  DIELTQSPASLSASVGETVTITCQASENIYSYLAWHQQKQGKSPQL...          46  129.7603   
1  DIQMTQSPSSLSASVGDRVTITCRASQDISNYLAWYQQKPGKAPKL...          45  115.9106   
2  DIQMTQSPSSVSASVGDRVTITCRASQGISSWLAWYQQKPGKAPKL...          45  109.6995   
3  DIQMTQSPSSVSASVGDRVTITCRASQGISSWLAWYQHKPGKAPKL...          49  112.6290   
4  DIQMTQSPSSLSASVGDRVTITCRASQGIRNYLAWYQQKPGKAPKL...          48  111.2512   

      PPC     PNC  SFvCSP  Y  
0  0.0000  0.0000   16.32  1  
1  0.0954  0.0421   -3.10  1  
2  0.0000  0.8965   -4.00  1  
3  0.0000  1.1247    3.10  1  
4  0.0485  1.1364  -19.50  1

In [6]:
chen_similarity = pd.read_csv(path.join(DATA_DIR, "chen/distances/deduplicated_anarci_similarity.csv"), index_col=0)
chen_similarity.head()

0        1        2        3        4        5        7        8  \
0  1.00000  0.77700  0.70350  0.69995  0.65085  0.67350  0.66915  0.66915   
1  0.77700  1.00000  0.75000  0.73500  0.69315  0.70240  0.65570  0.65570   
2  0.70350  0.75000  1.00000  0.76100  0.69315  0.68970  0.64550  0.64550   
3  0.69995  0.73500  0.76100  1.00000  0.66160  0.68700  0.65500  0.65500   
4  0.65085  0.69315  0.69315  0.66160  1.00000  0.63025  0.64000  0.64000   

         9       10  ...     2398     2400     2401     2402     2403  \
0  0.76100  0.71800  ...  0.59250  0.63185  0.65150  0.61850  0.70070   
1  0.74785  0.79775  ...  0.59600  0.65265  0.67200  0.63085  0.69350   
2  0.70850  0.72070  ...  0.55975  0.60500  0.65050  0.62120  0.69350   
3  0.68315  0.71335  ...  0.57800  0.63665  0.65900  0.61900  0.70700   
4  0.64965  0.68375  ...  0.62485  0.64180  0.60255  0.60010  0.67985   

      2404     2405     2406     2407     2408  
0  0.60550  0.54015  0.70460  0.61020  0.62840  
1  0.60750  0.55310  0.71665  0.63920  0.63185  
2  0.58815  0.55555  0.69965  0.57580  0.60875  
3  0.59300  0.54950  0.67185  0.58200  0.61370  
4  0.61990  0.54340  0.76250  0.62135  0.63570  

[5 rows x 1577 columns]

# Models

In [7]:
# different usage from the other models
def knn(n):
    model = NearestNeighbors(metric="precomputed")
    parameters = {'n_neighbors': [1,3,5]}
    return model, parameters, "kNN"

In [8]:
def logistic_regression(n):
    lr = LogisticRegression(class_weight='balanced', max_iter=1000, random_state=42)
    parameters = {'C':loguniform(0.001, 1000), 'penalty': ["l2"], "solver": ["lbfgs", "sag"]}
    return lr, parameters, "logistic_regression"

In [9]:
def random_forest(n):
    rf = RandomForestClassifier(random_state=42, n_jobs=-1, class_weight='balanced')
    parameters = {'n_estimators': np.arange(1, 200, 10), 'max_depth': np.arange(1, min(50,n), 2), 
                  'max_features': np.arange(0.1, 0.75, 0.05)}
    return rf, parameters, "random_forest"

In [10]:
def multilayer_perceptron(n):
    mlp = MLPClassifier(random_state=42, max_iter=int(1000))
    parameters = {'hidden_layer_sizes': [(100,), (50,), (100, 100)], "activation": ["relu", "logistic"]}
    return mlp, parameters, "multilayer_perceptron"

In [11]:
def svm(n):
    svc = SVC(max_iter=8000, probability=True, class_weight='balanced')
    parameters = {'C': loguniform(0.001, 100), 'kernel':["linear", "rbf"], 'gamma': loguniform(1e-3, 1e0)}
    return svc, parameters, "SVM"

In [12]:
def gradient_boosting(n):
    gb = GradientBoostingClassifier(random_state=42, n_iter_no_change=70)
    parameters = {'learning_rate': loguniform(0.01, 0.5), 
                  'n_estimators': np.arange(1, 200, 10), 
                  'max_depth': np.arange(1, min(20,n), 2), 
                  'max_features': np.arange(0.1, 0.6, 0.1)}
    return gb, parameters, "gradient_boosting"

In [13]:
def output_evaluation(model_type, params, metrics, data, outpath, preprocessing=None, table="all"):
    prepro = "_"+preprocessing if preprocessing is not None else ""
    filename = os.path.join(DATA_DIR, "evaluations", outpath, f"{model_type}_{data}{prepro}.json")
    out_dict = {
        "model_type": model_type,
        "data": data
    }
    out_dict["params"] = {}
    for key, value in params.items():
        out_dict["params"]["key"] = str(value)
    out_dict["metrics"] = metrics
    out_dict["preprocessing"] = "none" if preprocessing is None else preprocessing
    
    json.dump(out_dict, open(filename, "w"))
    
    filename_sum = os.path.join(DATA_DIR, f"evaluations/{outpath}/{table}.csv")
    #"../evaluations/all.csv"
    line = [model_type, data, out_dict["preprocessing"], metrics["f1"], metrics["mcc"], metrics["acc"],metrics["precision"],metrics["recall"],metrics["auc"], filename]
    with open(filename_sum, 'a', newline='') as csvfile:
        csvwriter = csv.writer(csvfile, delimiter='\t')
        csvwriter.writerow(line)

In [14]:
def train_and_eval(model_name, classifier, parameters, X_train, y_train, X_valid, y_valid, 
                   data_name, outpath, preprocessing=None):
    grid = RandomizedSearchCV(classifier, parameters, verbose=1, scoring="f1")
    grid.fit(X_train, y_train)
    estimator = grid.best_estimator_
    best_params = grid.best_params_
    y_pred = estimator.predict(X_valid)
    prepro = "_"+preprocessing if preprocessing is not None else ""
    filename = path.join(DATA_DIR, "evaluations", outpath, "models", f"{model_name}_{data_name}{prepro}.pkl")
    with open(filename, 'wb') as f:
        pickle.dump(estimator, f)
    #pickle.dump(estimator, open(filename, "w"))
    metric_dict = {
        "f1": float(metrics.f1_score(y_valid, y_pred)),
        "acc": float(metrics.accuracy_score(y_valid, y_pred)),
        "mcc": float(metrics.matthews_corrcoef(y_valid, y_pred)),
        "auc": float(metrics.roc_auc_score(y_valid, y_pred)),
        "precision": float(metrics.precision_score(y_valid, y_pred)),
        "recall": float(metrics.recall_score(y_valid, y_pred))
    }
    
    print(f"{model_name}, {data_name}")
    print(f"F1: {metric_dict['f1']}")
    print(f"MCC: {metric_dict['mcc']}")
    print(f"Accuracy: {metric_dict['acc']}")
    print(f"Precision: {metric_dict['precision']}")
    print(f"Recall: {metric_dict['recall']}")
    print(f"AUC: {metric_dict['auc']}")
    print(f"-----")
    
    output_evaluation(model_name, parameters, metric_dict, data_name, outpath, preprocessing=preprocessing)

In [15]:
def try_all(X_train, y_train, X_valid, y_valid, data_name, outpath, preprocessing=None):
    n = len(y_train)
    for model_creator in [logistic_regression, random_forest, gradient_boosting, svm, multilayer_perceptron]:
        classifier, params, model_label = model_creator(n)
        print("\n")
        print(f'Training model {model_label} on data {data_name} \n')
        train_and_eval(model_label, classifier, params, X_train, y_train, X_valid, y_valid, 
                   data_name, outpath, preprocessing=preprocessing)

In [16]:
def test_on_tap(model_name, x_test, y_test,
                   data_name, outpath, preprocessing=None):
    prepro = "_"+preprocessing if preprocessing is not None else ""
    filename = path.join(DATA_DIR, "evaluations", outpath, "models", f"{model_name}_{data_name}{prepro}.pkl")
    with open(filename, 'rb') as f:
        estimator = pickle.load(f)
    y_pred = estimator.predict(x_test)
    metric_dict = {
        "f1": float(metrics.f1_score(y_test, y_pred)),
        "acc": float(metrics.accuracy_score(y_test, y_pred)),
        "mcc": float(metrics.matthews_corrcoef(y_test, y_pred)),
        "auc": float(metrics.roc_auc_score(y_test, y_pred)),
        "precision": float(metrics.precision_score(y_test, y_pred)),
        "recall": float(metrics.recall_score(y_test, y_pred))
    }
    filename_sum = os.path.join(DATA_DIR, f"evaluations/{outpath}/tap.csv")
    line = [model_name, data_name, prepro, metric_dict["f1"], metric_dict["mcc"], metric_dict["acc"],metric_dict["precision"],metric_dict["recall"],metric_dict["auc"], filename]
    with open(filename_sum, 'a', newline='') as csvfile:
        csvwriter = csv.writer(csvfile, delimiter='\t')
        csvwriter.writerow(line)

In [17]:
def test_all(x_test, y_test, data_name, outpath, preprocessing=None):
    for model in ["logistic_regression", "random_forest", "gradient_boosting", "SVM", "multilayer_perceptron"]:
        print(f"Testing model {model} on {data_name}...")
        test_on_tap(model, x_test, y_test, data_name, outpath, preprocessing=preprocessing)

# PyBioMed

In [20]:
x_chen = pd.read_feather(path.join(DATA_DIR, "chen/pybiomed/X_data.ftr"))
x_chen_train = x_chen.loc[chen_train.index]
x_chen_test = x_chen.loc[chen_test.index]
x_chen_valid = x_chen.loc[chen_valid.index]
x_chen_train.head()

Ab_ID      0      1      2      3      4      5      6       7      8  \
2073  6aod  7.692  5.983  0.855  5.983  1.709  4.274  5.983  10.256  0.855   
1517  4yny  6.838  5.128  1.709  5.128  1.709  3.419  4.274  11.111  0.855   
2025  5xcv  6.838  5.128  1.709  5.128  2.564  3.419  4.274  11.111  0.855   
2070  6and  6.667  5.833  2.500  5.833  1.667  4.167  5.000  13.333  0.000   
666   2xqy  3.390  3.390  2.542  5.932  1.695  3.390  6.780   9.322  0.847   

      ...  19750  19751  19752  19753  19754  19755  19756  19757  19758  \
2073  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1517  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2025  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2070  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
666   ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   

      19759  
2073    0.0  
1517    0.0  
2025    0.0  
2070    0.0  
666     0.0  

[5 rows x 19761 columns]

In [21]:
scaler = StandardScaler()
scaler.fit(x_chen_train.drop("Ab_ID", axis=1))
x_chen_train = scaler.transform(x_chen_train.drop("Ab_ID", axis=1))
x_chen_valid = scaler.transform(x_chen_valid.drop("Ab_ID", axis=1))

In [22]:
x_tap = pd.read_feather(path.join(DATA_DIR, "tap/pybiomed/X_TAP_data.ftr"))
x_tap.head()

0      1      2      3      4      5      6       7      8      9  \
0  10.084  3.361  2.521  3.361  1.681  3.361  5.882  11.765  0.840  1.681   
1   7.627  4.237  1.695  3.390  1.695  5.085  5.932  10.169  0.847  2.542   
2   5.932  1.695  0.000  5.932  1.695  5.085  6.780  10.169  0.847  1.695   
3   5.738  6.557  4.098  5.738  1.639  3.279  4.918  11.475  0.820  3.279   
4   9.091  4.959  3.306  5.785  1.653  4.132  4.132   9.091  1.653  2.479   

   ...  19750  19751  19752  19753  19754  19755  19756  19757  19758  19759  
0  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0  
1  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0  
2  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0  
3  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0  
4  ...    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0  

[5 rows x 19760 columns]

In [23]:
#scaler = StandardScaler()
#scaler.fit(x_tap)
x_tap = scaler.transform(x_tap)

In [ ]:
try_all(x_chen_train, chen_train["Y"], x_chen_valid, chen_valid["Y"], "pybiomed", "2021-11-24", preprocessing="StandardScaler")



Training model logistic_regression on data pybiomed 

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [ ]:
test_all(x_tap, tap_data["Y"], "pybiomed", "2021-11-24", preprocessing="StandardScaler")

# Protparam

In [18]:
x_chen = pd.read_csv(path.join(DATA_DIR, "chen/protparam/protparam_features.csv"))
x_chen.rename({"Unnamed: 0": "Ab_ID"}, axis=1, inplace=True)
x_chen_train = x_chen.loc[chen_train.index]
x_chen_test = x_chen.loc[chen_test.index]
x_chen_valid = x_chen.loc[chen_valid.index]
x_chen_train.head()

Ab_ID  aa_percent0_x  aa_percent1_x  aa_percent2_x  aa_percent3_x  \
2073  1xiw       0.049180       0.016393       0.049180       0.040984   
1517  5b3j       0.057377       0.016393       0.032787       0.040984   
2025  1j1x       0.026549       0.017699       0.070796       0.026549   
2070  5f7e       0.067227       0.016807       0.050420       0.033613   
666   5b71       0.097561       0.016260       0.040650       0.032520   

      aa_percent4_x  aa_percent5_x  aa_percent6_x  aa_percent7_x  \
2073       0.032787       0.090164       0.008197       0.016393   
1517       0.024590       0.114754       0.000000       0.024590   
2025       0.008850       0.070796       0.000000       0.035398   
2070       0.033613       0.100840       0.008403       0.016807   
666        0.016260       0.113821       0.024390       0.016260   

      aa_percent8_x  ...  flexibility_y  isoelectric_y  mol_extinct1_y  \
2073       0.081967  ...       1.000398       6.756409           19940   
1517       0.040984  ...       1.001878       6.753845           17420   
2025       0.035398  ...       1.002679       6.911682           16960   
2070       0.042017  ...       1.004044       4.570740           14440   
666        0.040650  ...       1.006930       7.952576           12950   

      mol_extinct2_y        mw_y   gravy_y  ss_faction1_y  ss_faction2_y  \
2073           20065  11853.0516 -0.441121       0.289720       0.280374   
1517           17545  11736.0293 -0.425472       0.301887       0.301887   
2025           17085  11598.7277 -0.327103       0.280374       0.364486   
2070           14565  11255.3375 -0.405825       0.281553       0.300971   
666            13075  11559.6424 -0.365455       0.245455       0.354545   

      ss_faction3_y  name  
2073       0.168224  1xiw  
1517       0.160377  5b3j  
2025       0.158879  1j1x  
2070       0.145631  5f7e  
666        0.154545  5b71  

[5 rows x 64 columns]

In [21]:
scaler = StandardScaler()
scaler.fit(x_chen_train.drop(["Ab_ID", "name"], axis=1))
x_chen_train = scaler.transform(x_chen_train.drop(["Ab_ID", "name"], axis=1))
x_chen_valid = scaler.transform(x_chen_valid.drop(["Ab_ID", "name"], axis=1))

In [24]:
try_all(x_chen_train, chen_train["Y"], x_chen_valid, chen_valid["Y"], "protparam", "2021-11-24", preprocessing="StandardScaler")



Training model logistic_regression on data protparam 

Fitting 5 folds for each of 10 candidates, totalling 50 fits


/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_sag.py:329: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_sag.py:329: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_sag.py:329: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_sag.py:329: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_sag.py:3

logistic_regression, protparam
F1: 0.21582733812949642
MCC: -0.07383541481488283
Accuracy: 0.5439330543933054
Precision: 0.16666666666666666
Recall: 0.30612244897959184
AUC: 0.4556928034371644
-----


Training model random_forest on data protparam 

Fitting 5 folds for each of 10 candidates, totalling 50 fits
random_forest, protparam
F1: 0.22222222222222224
MCC: -0.021624952693064955
Accuracy: 0.6192468619246861
Precision: 0.19117647058823528
Recall: 0.2653061224489796
AUC: 0.48791621911922667
-----


Training model gradient_boosting on data protparam 

Fitting 5 folds for each of 10 candidates, totalling 50 fits
gradient_boosting, protparam
F1: 0.0923076923076923
MCC: -0.011624854861783338
Accuracy: 0.7531380753138075
Precision: 0.1875
Recall: 0.061224489795918366
AUC: 0.49640171858216975
-----


Training model SVM on data protparam 

Fitting 5 folds for each of 10 candidates, totalling 50 fits


/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_it

SVM, protparam
F1: 0.28169014084507044
MCC: 0.01983408273000735
Accuracy: 0.5732217573221757
Precision: 0.21505376344086022
Recall: 0.40816326530612246
AUC: 0.5119763694951666
-----


Training model multilayer_perceptron on data protparam 

Fitting 5 folds for each of 6 candidates, totalling 30 fits


/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/model_selection/_search.py:289: UserWarning: The total space of parameters 6 is smaller than n_iter=10. Running 6 iterations. For exhaustive searches, use GridSearchCV.
  % (grid_size, self.n_iter, grid_size), UserWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:617: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (1000) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:617: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (1000) reached and the optimization hasn't converged yet.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/neural_network/_multilayer_perceptron.py:617: ConvergenceWarning: Stochastic Optimizer: Maximum iteration

multilayer_perceptron, protparam
F1: 0.10810810810810809
MCC: -0.03811540585308798
Accuracy: 0.7238493723849372
Precision: 0.16
Recall: 0.08163265306122448
AUC: 0.48555316863587544
-----


In [ ]:
#test_all(x_tap, tap_data["Y"], "protparam", "2021-11-24", preprocessing="StandardScaler")

# BERT Embeddings

In [25]:
x_chen = pd.read_feather(path.join(DATA_DIR, "chen/embeddings/bert/bert_chen_embeddings.ftr"))
x_chen_train = x_chen.loc[chen_train.index]
x_chen_test = x_chen.loc[chen_test.index]
x_chen_valid = x_chen.loc[chen_valid.index]
x_chen_train.head()

Ab_ID         0         1         2         3         4         5  \
2073  6aod  0.020196 -0.020793 -0.010549 -0.038375  0.066936 -0.022921   
1517  4yny -0.007447 -0.058638  0.013139 -0.029136  0.074901 -0.025573   
2025  5xcv -0.005372 -0.056795  0.012577 -0.031566  0.071131 -0.023377   
2070  6and -0.004229 -0.043975  0.003673 -0.031739  0.070902 -0.022174   
666   2xqy  0.003754 -0.018278 -0.001506 -0.037899  0.050809 -0.026173   

             6         7         8  ...      2038      2039      2040  \
2073  0.017874 -0.088493 -0.018926  ...  0.001973 -0.003466 -0.014579   
1517  0.035983 -0.105274 -0.014490  ...  0.008387  0.007312 -0.013750   
2025  0.037339 -0.102565 -0.009340  ...  0.008306  0.003619 -0.015327   
2070  0.038274 -0.111665 -0.030382  ...  0.006203 -0.016125 -0.021334   
666   0.003026 -0.090757  0.005515  ... -0.003720  0.004341 -0.036547   

          2041      2042      2043      2044      2045      2046      2047  
2073  0.007682 -0.027888  0.026192 -0.040531 -0.010679  0.007133 -0.027332  
1517 -0.003369  0.007132  0.042410 -0.044542 -0.034221 -0.023036 -0.013044  
2025 -0.003542  0.003720  0.043285 -0.046977 -0.033989 -0.025775 -0.012205  
2070 -0.005837 -0.025217  0.024086 -0.032259 -0.023480 -0.013043 -0.035664  
666  -0.009119 -0.038372  0.023391 -0.030063 -0.003554  0.000142 -0.041985  

[5 rows x 2049 columns]

In [26]:
scaler = StandardScaler()
scaler.fit(x_chen_train.drop("Ab_ID", axis=1))
x_chen_train = scaler.transform(x_chen_train.drop("Ab_ID", axis=1))
x_chen_valid = scaler.transform(x_chen_valid.drop("Ab_ID", axis=1))

In [28]:
try_all(x_chen_train, chen_train["Y"], x_chen_valid, chen_valid["Y"], "bert", "2021-11-24", preprocessing="StandardScaler")



Training model logistic_regression on data bert 

Fitting 5 folds for each of 10 candidates, totalling 50 fits


/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_logistic.py:765: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  extra_warning_msg=_LOGISTIC_SOLVER_CONVERGENCE_MSG)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_logistic.py:765: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/

logistic_regression, bert
F1: 0.38095238095238093
MCC: 0.18215562599463012
Accuracy: 0.6736401673640168
Precision: 0.3116883116883117
Recall: 0.4897959183673469
AUC: 0.6054242749731472
-----


Training model random_forest on data bert 

Fitting 5 folds for each of 10 candidates, totalling 50 fits
random_forest, bert
F1: 0.40287769784172667
MCC: 0.20423323225159107
Accuracy: 0.6527196652719666
Precision: 0.3111111111111111
Recall: 0.5714285714285714
AUC: 0.6225563909774435
-----


Training model gradient_boosting on data bert 

Fitting 5 folds for each of 10 candidates, totalling 50 fits
gradient_boosting, bert
F1: 0.11594202898550723
MCC: -0.0037583683829191007
Accuracy: 0.7447698744769874
Precision: 0.2
Recall: 0.08163265306122448
AUC: 0.49871106337271753
-----


Training model SVM on data bert 

Fitting 5 folds for each of 10 candidates, totalling 50 fits


/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_it

SVM, bert
F1: 0.22222222222222224
MCC: 0.019083687059118202
Accuracy: 0.6778242677824268
Precision: 0.22
Recall: 0.22448979591836735
AUC: 0.5096133190118153
-----


Training model multilayer_perceptron on data bert 

Fitting 5 folds for each of 6 candidates, totalling 30 fits
multilayer_perceptron, bert
F1: 0.3404255319148936
MCC: 0.17958286109399652
Accuracy: 0.7405857740585774
Precision: 0.35555555555555557
Recall: 0.32653061224489793
AUC: 0.5869495166487647
-----


In [29]:
x_tap = pd.read_feather(path.join(DATA_DIR, "tap/embeddings/bert/bert_tap_embeddings.ftr"))
x_tap.head()

Ab_ID         0         1         2         3         4         5  \
0  Abagovomab -0.004248 -0.024501 -0.011330 -0.027170  0.062747 -0.024793   
1  Abituzumab  0.006593 -0.013591 -0.008454 -0.043601  0.065095 -0.016896   
2   Abrilumab  0.019445 -0.002642 -0.011395 -0.058757  0.060623 -0.015046   
3   Actoxumab -0.006365 -0.043729  0.005978 -0.025613  0.067748 -0.009542   
4  Adalimumab -0.012995 -0.035269  0.014127 -0.042136  0.080592 -0.012831   

          6         7         8  ...      2038      2039      2040      2041  \
0  0.009313 -0.083316 -0.005339  ... -0.008674 -0.002387 -0.021563  0.001087   
1 -0.001596 -0.090935 -0.002940  ...  0.000486 -0.013063 -0.021852 -0.003531   
2  0.006317 -0.083772 -0.006775  ...  0.005834 -0.017189 -0.014557  0.003359   
3  0.017723 -0.096801 -0.007752  ... -0.000024 -0.012986 -0.019753 -0.004326   
4  0.031889 -0.091308 -0.018166  ... -0.002067 -0.022957 -0.021145 -0.002762   

       2042      2043      2044      2045      2046      2047  
0 -0.020986  0.047104 -0.038736 -0.021780 -0.022153 -0.024539  
1 -0.024620  0.027387 -0.041001 -0.025708 -0.016437 -0.034342  
2 -0.035368  0.020287 -0.033941 -0.023549 -0.008720 -0.044038  
3 -0.044124  0.019544 -0.039559 -0.015679 -0.008837 -0.043877  
4 -0.058199  0.026781 -0.046815 -0.010110 -0.008785 -0.041761  

[5 rows x 2049 columns]

In [30]:
x_tap = scaler.transform(x_tap.drop("Ab_ID", axis=1))

In [31]:
test_all(x_tap, tap_data["Y"], "bert", "2021-11-24", preprocessing="StandardScaler")

Testing model logistic_regression on bert...
Testing model random_forest on bert...
Testing model gradient_boosting on bert...
Testing model SVM on bert...
Testing model multilayer_perceptron on bert...


# SeqVec Embeddings

In [32]:
x_chen = pd.read_feather(path.join(DATA_DIR, "chen/embeddings/seqvec/seqvec_chen_embeddings.ftr"))
x_chen_train = x_chen.loc[chen_train.index]
x_chen_test = x_chen.loc[chen_test.index]
x_chen_valid = x_chen.loc[chen_valid.index]
x_chen_train.head()

Ab_ID         0         1         2         3         4         5  \
2073  6aod  0.031640 -0.191203 -0.268825 -0.134525  0.097435  0.001770   
1517  4yny  0.063575 -0.219689 -0.285444 -0.134554  0.089054 -0.023122   
2025  5xcv  0.060840 -0.227532 -0.280555 -0.136953  0.091411 -0.028528   
2070  6and  0.062686 -0.220758 -0.278071 -0.137741  0.086655 -0.016114   
666   2xqy -0.000458 -0.200469 -0.269982 -0.138054  0.112663 -0.007346   

             6         7         8  ...      2038      2039      2040  \
2073  0.019496  0.118835 -0.136518  ...  0.104400 -0.013639  0.135580   
1517  0.004502  0.162193 -0.047376  ... -0.005196 -0.113235  0.048879   
2025  0.001440  0.166315 -0.045701  ... -0.005788 -0.112651  0.049541   
2070 -0.027874  0.158912 -0.119345  ...  0.041290 -0.032623  0.144864   
666   0.037440  0.075526 -0.178788  ... -0.020374 -0.059074  0.133179   

          2041      2042      2043      2044      2045      2046      2047  
2073  0.059035 -0.006357 -0.085073  0.009538 -0.000886 -0.016590 -0.071586  
1517  0.061190 -0.005911 -0.104957  0.026941  0.016444 -0.065021 -0.105957  
2025  0.063261 -0.005133 -0.104734  0.027340  0.017490 -0.064584 -0.105592  
2070  0.008824 -0.014455 -0.080329 -0.049089  0.033029 -0.017042 -0.044416  
666   0.018044  0.066013 -0.061189 -0.029644 -0.050942 -0.035482 -0.058019  

[5 rows x 2049 columns]

In [33]:
scaler = StandardScaler()
scaler.fit(x_chen_train.drop("Ab_ID", axis=1))
x_chen_train = scaler.transform(x_chen_train.drop("Ab_ID", axis=1))
x_chen_valid = scaler.transform(x_chen_valid.drop("Ab_ID", axis=1))

In [34]:
try_all(x_chen_train, chen_train["Y"], x_chen_valid, chen_valid["Y"], "seqvec", "2021-11-24", preprocessing="StandardScaler")



Training model logistic_regression on data seqvec 

Fitting 5 folds for each of 10 candidates, totalling 50 fits


/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_sag.py:329: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_sag.py:329: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_sag.py:329: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_sag.py:329: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/linear_model/_sag.py:3

logistic_regression, seqvec
F1: 0.40310077519379844
MCC: 0.21080214098455255
Accuracy: 0.6778242677824268
Precision: 0.325
Recall: 0.5306122448979592
AUC: 0.6232008592910849
-----


Training model random_forest on data seqvec 

Fitting 5 folds for each of 10 candidates, totalling 50 fits


/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/base.py:315: UserWarning: Trying to unpickle estimator DecisionTreeClassifier from version 1.0.1 when using version 0.24.2. This might lead to breaking code or invalid results. Use at your own risk.
  UserWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/base.py:333: UserWarning: Trying to unpickle estimator DecisionTreeClassifier from version 0.24.2 when using version 1.0.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/modules/model_persistence.html#security-maintainability-limitations
  UserWarning,
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/base.py:333: UserWarning: Trying to unpickle estimator RandomForestClassifier from version 0.24.2 when using version 1.0.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://sciki

random_forest, seqvec
F1: 0.20224719101123595
MCC: 0.022187174184243416
Accuracy: 0.702928870292887
Precision: 0.225
Recall: 0.1836734693877551
AUC: 0.5102577873254565
-----


Training model gradient_boosting on data seqvec 

Fitting 5 folds for each of 10 candidates, totalling 50 fits


/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/base.py:333: UserWarning: Trying to unpickle estimator DecisionTreeClassifier from version 0.24.2 when using version 1.0.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/modules/model_persistence.html#security-maintainability-limitations
  UserWarning,
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/base.py:333: UserWarning: Trying to unpickle estimator RandomForestClassifier from version 0.24.2 when using version 1.0.1. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/modules/model_persistence.html#security-maintainability-limitations
  UserWarning,
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/base.py:333: UserWarning: Trying to unpickle estimator DecisionTreeClassifier from version 0.24.2 when using ver

gradient_boosting, seqvec
F1: 0.16901408450704225
MCC: 0.05339910156767412
Accuracy: 0.7531380753138075
Precision: 0.2727272727272727
Recall: 0.12244897959183673
AUC: 0.5191192266380236
-----


Training model SVM on data seqvec 

Fitting 5 folds for each of 10 candidates, totalling 50 fits


/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/svm/_base.py:258: ConvergenceWarning: Solver terminated early (max_iter=8000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_it

SVM, seqvec
F1: 0.3366336633663366
MCC: 0.15922648841273856
Accuracy: 0.7196652719665272
Precision: 0.3269230769230769
Recall: 0.3469387755102041
AUC: 0.5813641245972072
-----


Training model multilayer_perceptron on data seqvec 

Fitting 5 folds for each of 6 candidates, totalling 30 fits
multilayer_perceptron, seqvec
F1: 0.2916666666666667
MCC: 0.1137915268000298
Accuracy: 0.7154811715481172
Precision: 0.2978723404255319
Recall: 0.2857142857142857
AUC: 0.5560150375939849
-----


In [35]:
x_tap = pd.read_feather(path.join(DATA_DIR, "tap/embeddings/seqvec/seqvec_tap_embeddings.ftr"))
x_tap.head()

Ab_ID         0         1         2         3         4         5  \
0  Abagovomab -0.004248 -0.024501 -0.011330 -0.027170  0.062747 -0.024793   
1  Abituzumab  0.006593 -0.013591 -0.008454 -0.043601  0.065095 -0.016896   
2   Abrilumab  0.019445 -0.002642 -0.011395 -0.058757  0.060623 -0.015046   
3   Actoxumab -0.006365 -0.043729  0.005978 -0.025613  0.067748 -0.009542   
4  Adalimumab -0.012995 -0.035269  0.014127 -0.042136  0.080592 -0.012831   

          6         7         8  ...      2038      2039      2040      2041  \
0  0.009313 -0.083316 -0.005339  ... -0.008674 -0.002387 -0.021563  0.001087   
1 -0.001596 -0.090935 -0.002940  ...  0.000486 -0.013063 -0.021852 -0.003531   
2  0.006317 -0.083772 -0.006775  ...  0.005834 -0.017189 -0.014557  0.003359   
3  0.017723 -0.096801 -0.007752  ... -0.000024 -0.012986 -0.019753 -0.004326   
4  0.031889 -0.091308 -0.018166  ... -0.002067 -0.022957 -0.021145 -0.002762   

       2042      2043      2044      2045      2046      2047  
0 -0.020986  0.047104 -0.038736 -0.021780 -0.022153 -0.024539  
1 -0.024620  0.027387 -0.041001 -0.025708 -0.016437 -0.034342  
2 -0.035368  0.020287 -0.033941 -0.023549 -0.008720 -0.044038  
3 -0.044124  0.019544 -0.039559 -0.015679 -0.008837 -0.043877  
4 -0.058199  0.026781 -0.046815 -0.010110 -0.008785 -0.041761  

[5 rows x 2049 columns]

In [36]:
x_tap = scaler.transform(x_tap.drop("Ab_ID", axis=1))

In [37]:
test_all(x_tap, tap_data["Y"], "seqvec", "2021-11-24", preprocessing="StandardScaler")

Testing model logistic_regression on seqvec...
Testing model random_forest on seqvec...
Testing model gradient_boosting on seqvec...
Testing model SVM on seqvec...


/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/metrics/_classification.py:873: RuntimeWarning: invalid value encountered in double_scalars
  <https://www.sciencedirect.com/science/article/pii/S1476927104000799>`_.
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/metrics/_classification.py:873: RuntimeWarning: invalid value encountered in double_scalars
  <https://www.sciencedirect.com/science/article/pii/S1476927104000799>`_.
/home/brazdilv/.conda/envs/ml/lib/python3.7/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  array([0.71..., 0.        , 0.        ])


Testing model multilayer_perceptron on seqvec...
